In [1]:
!pip install -q datasets loralib sentencepiece accelerate bitsandbytes
!pip install -q git+https://github.com/zphang/transformers@c3dc391
!pip install -q git+https://github.com/huggingface/peft.git

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 468.7/468.7 kB 12.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 45.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.3/215.3 kB 10.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 104.3/104.3 MB 10.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.2/212.2 kB 25.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 200.1/200.1 kB 22.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.9/132.9 kB 17.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 12.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 34.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 kB 14.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 264.6/264.6 kB 23.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.2/114.2 kB 14.9 MB/s eta 0:00:00
  Installing build dependencies 

In [3]:
import pickle
import tqdm
import pandas as pd
from peft import PeftModel
from transformers import LLaMATokenizer, LLaMAForCausalLM, GenerationConfig

# Alpaca-7B Model Initialization

In [2]:
tokenizer = LLaMATokenizer.from_pretrained("decapoda-research/llama-7b-hf")
model = LLaMAForCausalLM.from_pretrained(
    "decapoda-research/llama-7b-hf",
    load_in_8bit=True,
    device_map="auto",
)
model = PeftModel.from_pretrained(model, "tloen/alpaca-lora-7b")


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /usr/local/lib/python3.9/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so.11.0
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 118
CUDA SETUP: Loading binary /usr/local/lib/python3.9/dist-packages/bitsandbytes/libbitsandbytes_cuda118.so...


/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: /usr/lib64-nvidia did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/sys/fs/cgroup/memory.events /var/colab/cgroup/jupyter-children/memory.events')}
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('http'), PosixPath('//172.28.0.1'), PosixPath('8013')}
  warn(msg)
/usr/local/lib/python3.9/dist-packages/bitsandbytes/cuda_setup/main.py:145: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('//colab.research.google.com/tun/m/cc48301118ce

Overriding torch_dtype=None with `torch_dtype=torch.float16` due to requirements of `bitsandbytes` to enable model loading in mixed int8. Either pass torch_dtype=torch.float16 or don't pass this argument at all to remove this warning.


Loading checkpoint shards:   0%|          | 0/33 [00:00<?, ?it/s]

In [4]:
def generate_text_alpaca(model, tokenizer, prompt, temperature=0.1, top_p=1, max_new_tokens=512):
    """Generate text using the Alpaca-7B model using the input prompt."""
    
    inputs = tokenizer(prompt, return_tensors="pt")
    input_ids = inputs["input_ids"].cuda()
    generation_output = model.generate(
        input_ids=input_ids,
        temperature=0.1,
        top_p=0.75,
        max_new_tokens=2048,
    )
    output = tokenizer.decode(generation_output[0], skip_special_tokens=True)
    edited_output_text = output.split("### Response:")[1].strip()
    return edited_output_text

# Prompt Templates

In [5]:
def generate_alpaca_prompt(query, context):
    prompt_template = f"""Below is an instruction that describes a task, paired with an input that provides further context. Use the following guidelines to write a response that that appropriately completes the request:
### Instruction:
- Write a detailed paragraph consisting of exactly five complete sentences that answer the question based on the provided context.
- Focus on addressing the specific question posed, providing as much relevant information and detail as possible.
- Only use details from the provided context that directly address the question; do not include any additional information that is not explicitly stated.
- Aim to provide a clear and concise summary that fully addresses the question.

Question: {query}
Context: {context}
### Response:"""
    return prompt_template


def generate_alpaca_prompt_few_shot_1(query, context):
    """Creates a prompt with few shot examples of Nvidia and Intel."""
    prompt = f"""Below is an instruction that describes a task, paired with an input that provides further context. Use the following guidelines to write a response that that appropriately completes the request:
### Instruction:
- Write a detailed paragraph consisting of exactly five complete sentences that answer the question based on the provided context.
- Focus on addressing the specific question posed, providing as much relevant information and detail as possible.
- Only use details from the provided context that directly address the question; do not include any additional information that is not explicitly stated.
- Aim to provide a clear and concise summary that fully addresses the question.
- Use the following examples as a guide to structure your response:

    Example-1:
      Question: What is Nvidia's visibility in the data center business?
      Context: People still saw it as something esoteric. But today, data centers all over the world expect a very significant part of their data center being accelerated with GPUs. The number of workloads that we've accelerated since in the last 5 years have expanded tremendously, whether it's imaging or video or conversational AI or deep recommender systems that probably unquestionably, at this point, the most important machine learning model in the world. When we came -- when we started to introduce Ampere to the data center, it was very commonsensical to them that they would adopt it. They have a large amount of workload that's already accelerated by NVIDIA GPUs. And as you know, our GPUs are architecturally compatible from generation to generation. And I think every nation and government and scientific lab is now gearing up to think about what does it take to create a national defense system for each country that is based on computational methods? And NVIDIA is an accelerated computing company. We take something that otherwise would take a year in the case of Oak Ridge, and they filter 1 billion compounds in a day. And so notice, I've said 3 different architecture in a data center today. Most data centers today has a storage server, has CPU servers, and it has scale-up acceleration service with Voltas has scaled out servers with GeForce and then it has scale cloud computing, flexible servers based on V100. And so the ability to predict workload is so hard, and therefore, the utilization of these systems will be spiky. And then the second thing is we'd like to be able to innovate across the entire stack. You know that NVIDIA is just supremely obsessed about software stacks. And the reason for that is because software creates markets.
      Answer: Nvidia has become a very significant part of the data center business in the last 5 years, with its GPUs being used to accelerate a wide range of workloads, from imaging and video to conversational AI and deep recommender systems. Data centers have been quick to adopt Nvidia's Ampere architecture, as it is architecturally compatible with previous generations of GPUs. Nvidia is also being used to create national defense systems for countries, with Oak Ridge National Laboratory using it to filter 1 billion compounds in a day. Data centers today typically have a combination of storage servers, CPU servers, and scale-up acceleration servers with Volta and GeForce, as well as scale cloud computing servers based on V100. Nvidia is focused on software stacks, as they believe software creates markets. Overall, Nvidia has become a major player in the data center business, with its GPUs being used to accelerate a wide range of workloads and its software stacks creating markets.

    Example-2:
      Question: What is the update on the server chip roadmap and strategy?
      Context: Navin, any... Maybe the only thing I'd add, John, is that from a product point of view, the dynamic to think about in 2019 is that, as Bob mentioned, we began shipping for production Cascade Lake, our next-generation Xeon. And really, that product is going to ramp -- start to ramp in the middle part of the year and into the second half of the year. The product features look very compelling. The AI capability we have with DL Boost, the support for Optane persistent memory, the security, hardware mitigation fixes, so that the customer momentum around that product line looks very strong. But it really doesn't ramp until the middle to the second half of the year. During the course of '19, our expectations are, of that mix, that we'll be more logic-oriented. And that's really driven by a couple of things: one, ensuring we have the capacity to meet the 14-nanometer demand for our customers; secondly, as we ramp 10-nanometer in 2019 and position for 10- in 2020, we'll invest additional capital there; and then third, obviously, our expectations are to continue to invest in next-node technology, in particular, 7-nanometer. So logic capital is going to be going up year-on-year. Again, 10-nanometer ramp, not really any different. I highlighted in the prepared remarks, we feel very good about kind of where we are in ramping 10-nanometer during the course of the year to get systems on the shelf for the holiday season, so no real change there. And modem and memory growth will be a little bit slower today versus where we were 90 days ago. I think, as Bob said, and I think we talked about a little bit, we had 3 quarters of really, really strong growth in 2018 in the cloud. And that was driven by a product cycle as well as a typical multiyear build-out pattern with Xeon Scalable. And if you look back at all the historical trends we've had in the cloud business, we've always said there's some lumpiness to the business.
      Answer: Intel began shipping for production Cascade Lake, their next-generation Xeon, in 2019 and the product features look very compelling with AI capability, support for Optane persistent memory, and security hardware mitigation fixes. The product is expected to ramp up in the middle part of the year and into the second half of the year. Intel is investing in 14-nanometer capacity to meet customer demand, 10-nanometer technology for 2019 and 2020, and 7-nanometer technology. Logic capital is expected to increase year-on-year. Intel is investing in 10-nanometer technology to get systems on the shelf for the holiday season. Modem and memory growth is expected to be slower than it was 90 days ago due to the 3 quarters of strong growth in 2018 in the cloud.

Question: {query}
Context: {context}
### Response:"""
    return prompt


def generate_alpaca_prompt_few_shot_2(query, context):
    """Creates a prompt with few shot examples of Apple and AMD."""
    prompt = f"""Below is an instruction that describes a task, paired with an input that provides further context. Use the following guidelines to write a response that that appropriately completes the request:
### Instruction:
- Write a detailed paragraph consisting of exactly five complete sentences that answer the question based on the provided context.
- Focus on addressing the specific question posed, providing as much relevant information and detail as possible.
- Only use details from the provided context that directly address the question; do not include any additional information that is not explicitly stated.
- Aim to provide a clear and concise summary that fully addresses the question.
- Use the following examples as a guide to structure your response:

    Example-1:
      Question: What was discussed regarding Wearables revenue performance?
      Context: Products revenue $79.1b.               Up 8%, as iPhone returned to growth. Had incredibly strong results in Wearables, where Co. set all-time records for Apple Watch and AirPods. Services revenue grew 17% to new all-time record $12.7b with double-digit growth in every geographic segment, a new all-time records across portfolio. Among consumers and businesses, planning to purchase tablets in March qtr., 78% plan to purchase iPads. Wearables, Home & Accessories:          Established new all-time record with revenue of $10b, up 37% YoverY with strong double-digit performance across all five geographic segments and growth across Wearables, Accessories and Home.          Set all-time records for Wearables in virtually every market Co. tracks, even as it experienced some product shortages due to strong customer demand for Apple Watch and AirPods during the qtr.          Continued to see strong demand for products in enterprise market, as technology solutions enabled businesses to do their best work.               100% of Fortune 500 companies in healthcare sector use AAPL technology in areas like patient experience, clinical communications and nursing workflows.               Seeing smaller companies in this sector drive innovation with technology and apps.                    One example is Gauss Surgical, which uses Core ML in iOS to more accurately estimate blood loss during childbirth and surgery. This helps clinicians have more complete and timely information on whether a patient needs an intervention, which can impact both clinical outcomes and costs. Amit, it's Tim. If you look at the Apple -- or the Wearables as a category within the Wearables, Home and Accessories revenue, Wearables grew 44%, so it was very strong, as you say. The -- both Apple Watch and AirPods did very well in terms of collecting new customers. Apple Watch, in particular, 75% of the customers are new to the Apple Watch, and so it's still very much selling to new customers at this point. For the results from last quarter, we had double-digit growth for iPhone in Mainland China, so that was an important change from where we had been running. We also had double-digit growth in Services in Mainland China, and we had extremely strong double-digit on Wearables. And so really, there were a number of different factors.
      Answer: Wearables revenue was part of the overall Products revenue of $79.1b, which was up 8%. Wearables, Home & Accessories revenue established a new all-time record with revenue of $10b, up 37% year-over-year. Wearables experienced strong double-digit performance across all five geographic segments and growth across Wearables, Accessories and Home. Apple Watch and AirPods set all-time records for Wearables in virtually every market the company tracks, despite some product shortages due to strong customer demand. Apple Watch had 75% of customers being new to the product. Wearables had double-digit growth in Mainland China.

    Example-2:
      Question: How has the growth been for the PC market?
      Context: Yes. So when we look at the PC market, we finished 2019 very strong in the overall PC market, both mobile and desktop. I think that's primarily on the strength of the product portfolio and the expanding customer platforms that we have. So let me talk first about the market, and then talk a little bit about how we're seeing the full year. So if you look at the PC market, I think, the discussion so far has been, let's call it, 2020, flat to maybe down slightly. There has been some concern raised about the second half of '20 perhaps be weakened -- weaker than normal seasonality just due to some of the enterprise refresh cycles that are strong in the first half. So we feel good about that. In the data center market, again, I would say that the growth of computing continues. From our standpoint, we see it as a good market environment for data center in both cloud as well as enterprise. I think the CPU opportunity is very immediate and in front of us as we look at the opportunities with Rome and the expanding opportunities. I think the data center GPU market continues to be an important growth vector for us, and now I call that over the several-year horizon. So when you look at the opportunities that we have, when we combine our CPU and GPU IP together, they're very, very strong. So I'm not sure I'm going to forecast a share target for 2020. I will say though, if you take a look back at the last 8 quarters, we've been on a fairly steady share gain in PCs, somewhere between -- depending on the quarter, let's call it, 50 to 100 basis points per quarter, and that changes between desktop and notebook. I think we grew somewhere on the order of 4 points a share.
      Answer: AMD finished 2019 very strong in the overall PC market, both mobile and desktop, primarily due to the strength of their product portfolio and expanding customer platforms. The discussion for 2020 is that the PC market will be flat to slightly down, due to some concern about weaker than normal seasonality in the second half of the year. The data center market is a good environment for AMD, with CPU opportunities being very immediate and GPU opportunities being a growth vector over the next several years. Over the last 8 quarters, AMD has seen a steady share gain in PCs, ranging from 50 to 100 basis points per quarter, and growing 4 points of share overall. This share gain has been seen in both desktop and notebook PCs. AMD has seen strong growth in the PC market due to their product portfolio and expanding customer platforms, as well as their CPU and GPU IP.

Question: {query}
Context: {context}
### Response:"""
    return prompt


- The data for the Query and corresponding Context from the MPNET PineCone Index as been stored in a csv file. The context for the following queries was generated and stored in the csv file using another script.

- We load the Query, Context pairs from the CSV use that to generate the prompts.

In [6]:
query_data = [
    (
        "What was discussed regarding the Wearables revenue performance?",
        "2020",
        "Q1",
        "Company Speaker",
        "AAPL"
    ),
    (
        "How has the growth been for AMD in the PC market?",
        "2020",
        "Q1",
        "Company Speaker",
        "AMD"
    ),
    (
        "What is Nvidia's visibility in the data center business?",
        "2020",
        "Q2",
        "Company Speaker",
        "NVDA"
    ),
    (
        "What is the update on the server chip roadmap and strategy?",
        "2019",
        "Q1",
        "Company Speaker",
        "INTC"
    ),
    (
        "What are the opportunities and challenges in the Indian market?",
        "2016",
        "Q3",
        "Company Speaker",
        "AMZN"
    ),
   ]
index_data = pd.read_csv(r"https://huggingface.co/spaces/awinml/2-qa-earnings-sentencewise/raw/main/train_data.csv")

#Creating the prompts based on the stored Query, Context Pairs.

In [7]:
alpaca_zeroshot_prompts = []
alpaca_twoshot_prompts = []

for _, row in index_data.iterrows():
    query_text, context, ticker = tuple(row)
    zeroshot_prompt = generate_alpaca_prompt(query_text, context)
    if ticker in ["AAPL", "AMD"]:
        prompt = generate_alpaca_prompt_few_shot_1(query_text, context)
    elif ticker in ["NVDA", "INTC", "AMZN"]:
        prompt = generate_alpaca_prompt_few_shot_2(query_text, context)
    else: 
        prompt = generate_alpaca_prompt(query_text, context)
    alpaca_zeroshot_prompts.append((zeroshot_prompt, query_text, context))
    alpaca_twoshot_prompts.append((prompt, query_text, context))

# Generating Outputs with Zero Shot Prompts

In [9]:
generated_data_zero_shot = {}

for prompt, query_text, context_text in alpaca_zeroshot_prompts:
    print(query_text)
    generated_text = generate_text_alpaca(model, tokenizer, prompt)
    generated_data_zero_shot[query_text] = [generated_text, prompt, context_text]

What was discussed regarding the Wearables revenue performance?
How has the growth been for AMD in the PC market?
What is Nvidia's visibility in the data center business?
What is the update on the server chip roadmap and strategy?
What are the opportunities and challenges in the Indian market?


In [10]:
generated_df_zeroshot = pd.DataFrame.from_dict(generated_data_zero_shot, orient='index',
                       columns=['Generated_Text', 'Prompt', 'Context'])
generated_df_zeroshot.to_csv("alpaca_zeroshot_outputs.csv", index=False)

# Displaying the Generated Text

In [11]:
for i in range(0, len(generated_df_zeroshot.Generated_Text)):
    print(generated_df_zeroshot.Generated_Text[i], sep='\n--------------------')

The Wearables revenue performance was strong, with Apple Watch and AirPods setting all-time records. Apple Watch had a 75% customer base of new customers, while AirPods had a 50% customer base of new customers. Apple Watch and AirPods also experienced product shortages due to strong customer demand, but this did not hinder the overall revenue performance. The Wearables, Home and Accessories revenue grew 44%, with strong double-digit growth in all five geographic segments. Additionally, Apple saw strong demand from enterprise customers, with technology solutions enabling businesses to do their best work. One example is Gauss Surgical, which uses Core ML in iOS to more accurately estimate blood loss during childbirth and surgery. This helps clinicians have more complete and timely information on whether a patient needs an intervention, which can impact both clinical outcomes and costs.
AMD has seen strong growth in the PC market, both mobile and desktop, due to the strength of its produc

# Generating Outputs with Two Shot Prompts

In [12]:
generated_data_two_shot = {}

for prompt, query_text, context_text in alpaca_twoshot_prompts:
    print(query_text)
    generated_text = generate_text_alpaca(model, tokenizer, prompt)
    generated_data_two_shot[query_text] = [generated_text, prompt, context_text]

What was discussed regarding the Wearables revenue performance?
How has the growth been for AMD in the PC market?
What is Nvidia's visibility in the data center business?
What is the update on the server chip roadmap and strategy?
What are the opportunities and challenges in the Indian market?


In [13]:
generated_df_twoshot = pd.DataFrame.from_dict(generated_data_two_shot, orient='index',
                       columns=['Generated_Text', 'Prompt', 'Context'])
generated_df_twoshot.to_csv("alpaca_twoshot_outputs.csv", index=False)

# Displaying the Generated Text

In [14]:
for i in range(0, len(generated_df_twoshot.Generated_Text)):
    print(generated_df_twoshot.Generated_Text[i], sep='\n--------------------')

Wearables revenue grew 44% in the quarter, driven by strong double-digit growth in all five geographic segments. Apple Watch and AirPods both set all-time records for the category. Apple Watch saw strong double-digit growth in all five geographic segments, with particularly strong growth in the US, Japan and China. AirPods also saw strong double-digit growth in all five geographic segments, with particularly strong growth in the US, Japan and China.
AMD has seen strong growth in the PC market in 2019, both in mobile and desktop. The company expects the PC market to be flat to slightly down in 2020, but sees opportunities in the data center market, as well as the CPU and GPU markets. AMD has been on a steady share gain in the PC market, with gains of 50-100 basis points per quarter, depending on the quarter. The company has seen growth of 4 points in the overall PC market.
Nvidia has a strong presence in the data center business, with people seeing it as a more mainstream technology. Da